In [10]:
import pandas as pd
import csv
import regex as re
import nltk
from collections import Counter, defaultdict
import string
import unicodedata

def clean_text(text): 
    return re.sub(r"\p{P}", "", str(text).lower().replace("-\\n", "").replace("\\n", " "))

def train_model(data, model):
    for _, row in data.iterrows():
        words = nltk.word_tokenize(clean_text(row["final"]))
        for w1, w2 in nltk.bigrams(words, pad_left=True, pad_right=True):
            if w1 and w2:
                model[w2][w1] += 1
    for w2 in model:
        total_count = float(sum(model[w2].values()))
        for w1 in model[w2]:
            model[w2][w1] /= total_count


def predict(word, model):
    predictions = dict(model[word])
    most_common = dict(Counter(predictions).most_common(5))

    total_prob = 0.0
    str_prediction = ""

    for word, prob in most_common.items():
        total_prob += prob
        str_prediction += f"{word}:{prob} "

    if not total_prob:
        return "the:0.2 be:0.2 to:0.2 of:0.1 and:0.1 a:0.1 :0.1"

    if 1 - total_prob >= 0.01:
        str_prediction += f":{1-total_prob}"
    else:
        str_prediction += f":0.01"

    return str_prediction


def predict_data(read_path, save_path, model):
    data = pd.read_csv(
        read_path,
        sep="\t",
        error_bad_lines=False,
        header=None,
        quoting=csv.QUOTE_NONE,
        encoding="utf8"
    )
    with open(save_path, "w") as file:
        for _, row in data.iterrows():
            words = nltk.word_tokenize(clean_text(row[7]))
            if len(words) < 3:
                prediction = "the:0.2 be:0.2 to:0.2 of:0.1 and:0.1 a:0.1 :0.1"
            else:
                prediction = predict(words[-1], model)
            file.write(prediction + "\n")


In [11]:
with open("in-header.tsv") as f:
    in_cols = f.read().strip().split("\t")

with open("out-header.tsv") as f:
    out_cols = f.read().strip().split("\t")

In [12]:
in_cols

['FileId', 'Year', 'LeftContext', 'RightContext']

In [13]:
out_cols

['Word']

In [7]:
data = pd.read_csv(
    "train/in.tsv.xz",
    sep="\t",
    on_bad_lines='skip',
    header=None,
    # names=in_cols,
    quoting=csv.QUOTE_NONE,
)

train_words = pd.read_csv(
    "train/expected.tsv",
    sep="\t",
    on_bad_lines='skip',
    header=None,
    # names=out_cols,
    quoting=csv.QUOTE_NONE,
)

train_data = data[[7, 6]]
train_data = pd.concat([train_data, train_words], axis=1)

train_data["final"] = train_data[7] + train_data[0] + train_data[6]


In [8]:
train_data

7  \
0       said\nit's all squash. The best I could get\ni...   
1       \ninto a proper perspective with those\nminor ...   
2       all notU\nashore and afloat arc subjects for I...   
3       ceucju l< d no; <o waste it nud so\nsunk it in...   
4       ascertained w? OCt the COOltS of ibis\nletale ...   
...                                                   ...   
432017  \nSam was arrested.\nThe case excited a great ...   
432018  through the alnp the »Uitors laapeeeed tia.»\n...   
432019  Agua Negra across the line.\nIt was a grim pla...   
432020  \na note of Wood, Dialogue fc Co., for\nc27,im...   
432021  3214c;do White at 3614c: Mixed Western at\n331...   

                                                        6         0  \
0       came fiom the last place to this\nplace, and t...       lie   
1       MB. BOOT'S POLITICAL OBEED\nAttempt to imagine...   himself   
2       "Thera were in 1771 only aeventy-nine\n*ub*erl...        of   
3       A gixnl man y nitereRtiiiv dii-clos-\nur«s reg...      ably   
4       Tin: 188UB TV THF BBABBT QABJE\nMr. Schiffs *t...         j   
...                                                   ...       ...   
432017  Sam Clendenin bad a fancy for Ui«\nscience of ...       and   
432018  Wita.htt halting the party ware dilven to the ...  paasliic   
432019  It was the last thing that either of\nthem exp...       for   
432020  settlement with the department.\nIt is also sh...       for   
432021  Flour quotations—low extras at 1 R0®2 50;\ncit...        at   

                                                    final  
0       said\nit's all squash. The best I could get\ni...  
1       \ninto a proper perspective with those\nminor ...  
2       all notU\nashore and afloat arc subjects for I...  
3       ceucju l< d no; <o waste it nud so\nsunk it in...  
4       ascertained w? OCt the COOltS of ibis\nletale ...  
...                                                   ...  
432017  \nSam was arrested.\nThe case excited a great ...  
432018  through the alnp the »Uitors laapeeeed tia.»\n...  
432019  Agua Negra across the line.\nIt was a grim pla...  
432020  \na note of Wood, Dialogue fc Co., for\nc27,im...  
432021  3214c;do White at 3614c: Mixed Western at\n331...  

[432022 rows x 4 columns]

In [14]:

model = defaultdict(lambda: defaultdict(lambda: 0))

train_model(train_data, model)

C:\Users\Norbert\AppData\Local\Temp\ipykernel_15436\842062938.py:47: FutureWarning: The error_bad_lines argument has been deprecated and will be removed in a future version. Use on_bad_lines in the future.


  data = pd.read_csv(
C:\Users\Norbert\AppData\Local\Temp\ipykernel_15436\842062938.py:47: FutureWarning: The error_bad_lines argument has been deprecated and will be removed in a future version. Use on_bad_lines in the future.


  data = pd.read_csv(


UnicodeEncodeError: 'charmap' codec can't encode character '\u03b2' in position 21: character maps to <undefined>

In [15]:
predict_data("dev-0/in.tsv.xz", "dev-0/out.tsv", model)

C:\Users\Norbert\AppData\Local\Temp\ipykernel_15436\842062938.py:47: FutureWarning: The error_bad_lines argument has been deprecated and will be removed in a future version. Use on_bad_lines in the future.


  data = pd.read_csv(


In [ ]:
predict_data("test-A/in.tsv.xz", "test-A/out.tsv", model)